In [ ]:
# Note: restart runtime after this import before running the augmentations
!pip install -U augly
!sudo apt-get install python3-magic

     |████████████████████████████████| 40.1MB 76kB/s 
     |████████████████████████████████| 399kB 44.1MB/s 
     |████████████████████████████████| 11.6MB 28.5MB/s 
     |████████████████████████████████| 25.3MB 125kB/s 
     |████████████████████████████████| 3.0MB 35.0MB/s 
     |████████████████████████████████| 3.2MB 26.9MB/s 
     |████████████████████████████████| 61kB 8.4MB/s 
     |████████████████████████████████| 81kB 10.3MB/s 
     |████████████████████████████████| 27.4MB 110kB/s 
     |████████████████████████████████| 51.0MB 59kB/s 
     |████████████████████████████████| 3.4MB 25.6MB/s 
     |████████████████████████████████| 1.9MB 25.9MB/s 
     |████████████████████████████████| 829kB 39.6MB/s 
     |████████████████████████████████| 645kB 35.4MB/s 
     |████████████████████████████████| 184kB 44.8MB/s 
     |████████████████████████████████| 22.3MB 1.5MB/s 
     |████████████████████████████████| 430kB 34.2MB/s 
     |████████████████████████████████| 112kB 54.6MB

Reading package lists... Done
Building dependency tree       
Reading state information... Done
The following additional packages will be installed:
  libmagic-mgc libmagic1
Suggested packages:
  file
The following NEW packages will be installed:
  libmagic-mgc libmagic1 python3-magic
0 upgraded, 3 newly installed, 0 to remove and 39 not upgraded.
Need to get 262 kB of archives.
After this operation, 5,257 kB of additional disk space will be used.
Get:1 http://archive.ubuntu.com/ubuntu bionic-updates/main amd64 libmagic-mgc amd64 1:5.32-2ubuntu0.4 [184 kB]
Get:2 http://archive.ubuntu.com/ubuntu bionic-updates/main amd64 libmagic1 amd64 1:5.32-2ubuntu0.4 [68.6 kB]
Get:3 http://archive.ubuntu.com/ubuntu bionic/main amd64 python3-magic all 2:0.4.15-1 [9,280 B]
Fetched 262 kB in 1s (279 kB/s)
debconf: unable to initialize frontend: Dialog
debconf: (No usable dialog-like program is installed, so the dialog based frontend cannot be used. at /usr/share/perl5/Debconf/FrontEnd/Dialog.pm line 76

In [ ]:
# Installing ffmpeg is only needed for the video module of augly
!sudo add-apt-repository ppa:jonathonf/ffmpeg-4
!apt install ffmpeg

 Backport of FFmpeg 4 and associated libraries. Now includes AOM/AV1 support!

FDK AAC is not compatible with GPL and FFmpeg can't be redistributed with it included. Please don't ask for it to be added to this public PPA.

---

PPA supporters:

BigBlueButton (https://bigbluebutton.org)

---

Donate to FFMPEG: https://ffmpeg.org/donations.html
Donate to Debian: https://www.debian.org/donations
Donate to this PPA: https://ko-fi.com/jonathonf
 More info: https://launchpad.net/~jonathonf/+archive/ubuntu/ffmpeg-4
Press [ENTER] to continue or Ctrl-c to cancel adding it.

Hit:1 https://cloud.r-project.org/bin/linux/ubuntu bionic-cran40/ InRelease
Ign:2 https://developer.download.nvidia.com/compute/cuda/repos/ubuntu1804/x86_64  InRelease
Get:3 http://security.ubuntu.com/ubuntu bionic-security InRelease [88.7 kB]
Ign:4 https://developer.download.nvidia.com/compute/machine-learning/repos/ubuntu1804/x86_64  InRelease
Get:5 https://developer.download.nvidia.com/compute/cuda/repos/ubuntu1804/x86_64

In [ ]:
from IPython.display import display, HTML
from base64 import b64encode

def display_video(path):
  mp4 = open(path,'rb').read()
  data_url = "data:video/mp4;base64," + b64encode(mp4).decode()
  display(
    HTML(
      """
          <video width=400 controls>
                <source src="%s" type="video/mp4">
          </video>
      """ % data_url
    )
  )

In [ ]:
import os
import augly.utils as utils
import augly.video as vidaugs

# Get input video, trim to first 3 seconds
input_video = os.path.join(
    utils.TEST_URI, "video", "inputs", "input_1.mp4"
)
input_vid_path = "/tmp/in_video.mp4"
out_vid_path = "/tmp/aug_video.mp4"

# We can use the AugLy trim augmentation, and save the trimmed video
vidaugs.trim(input_video, output_path=input_vid_path, start=0, end=3)
display_video(input_vid_path)

In [ ]:
# Now we can apply various augmentations to the trimmed video!
vidaugs.overlay_text(input_vid_path, out_vid_path)
display_video(out_vid_path)

In [ ]:
"""
You can optionally pass in a metadata list, to which metadata about the
augmentation will be appended, including kwargs, input & output dimensions,
the matching segments in the input & output videos (useful in case of temporal
editing), and intensity (defined based on the kwargs for each augmentation).
"""
meta = []
vidaugs.loop(
    input_vid_path,
    out_vid_path,
    num_loops=1,
    metadata=meta,
)
display_video(out_vid_path)
meta

[{'dst_duration': 6.050139,
  'dst_fps': 29.916666666666668,
  'dst_height': 1080,
  'dst_segments': [OrderedDict([('start', 0.0), ('end', 3.008357)]),
   OrderedDict([('start', 3.008357), ('end', 6.016714)])],
  'dst_width': 1920,
  'intensity': 1.0,
  'name': 'loop',
  'num_loops': 1,
  'src_duration': 3.008357,
  'src_fps': 29.916666666666668,
  'src_height': 1080,
  'src_segments': [OrderedDict([('start', 0.0), ('end', 3.008357)]),
   OrderedDict([('start', 0.0), ('end', 3.008357)])],
  'src_width': 1920}]

In [ ]:
# You can also compose several transformations together
aug = vidaugs.Compose(
    [
        vidaugs.AddNoise(),
        vidaugs.Blur(sigma=5.0),
        vidaugs.OverlayDots(),
    ]
)
aug(input_vid_path, out_vid_path)
display_video(out_vid_path)

In [ ]:
# Testez d'autres transformations: https://github.com/facebookresearch/AugLy/blob/main/augly/video/__init__.py